<b><h1>IBM Applied Data Science Capstone Course</h1></b><br>
<h2>Week 5 Project</h2><br>
Opening a new Shopping Mall in Sydney
<ul>
<li>Build a dataframe of neighborhoods in Sydney by web scraping.</li>
<li>Get the geographical coordinates of the neighborhoods.</li>
<li>Obtain the venue data for the neighborhoods from Foursquare API.</li>
<li>Explore and cluster the neighborhoods.</li>
<li>Select the best cluster to open a new shopping mall.</li>
</ul>

<b><h3>1.Importing Libraries</h3></b>

In [1]:
import numpy as np
import pandas as pd
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)
import json
from geopy.geocoders import Nominatim #convert an address into latitude and longitude values
import geocoder #to get coordinates
import requests #library to handle requests
from bs4 import BeautifulSoup #library to parse HTML and XML documents
from pandas.io.json import json_normalize #tranform JSON file into a pandas dataframe
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
import folium
print("Libraries imported.")

Libraries imported.


<b><h3>2.Scrap data from Wikipedia</h3><b>

In [2]:
#Get request
data=requests.get("https://en.wikipedia.org/wiki/List_of_Sydney_suburbs").text

In [3]:
soup=BeautifulSoup(data,'html.parser')

In [4]:
#list to store neighborhood data
neighborList=[]
for i in range(5,len(soup.find_all('p'))):
    for row in soup.find_all('p')[i].find_all('a'):
        neighborList.append(row.text)

In [5]:
#Creating a dataframe for Sydney neighbourhoods
sy_df = pd.DataFrame({"Neighbourhood": neighborList})
sy_df.head()

Neighbourhood
0      Abbotsbury
1      Abbotsford
2  Acacia Gardens
3     Agnes Banks
4           Airds

In [6]:
#print the number of rows of the dataframe
sy_df.shape

(689, 1)

<b><h3>3.Get neighbourhood coordinates</h3></b>

In [7]:
#Read the csv file for Sydney neighbourhood coordinates
lat_long_df=pd.read_csv(r'/content/sample_data/Australia_Lat_Lon.csv')

In [8]:
lat_long_df.head()

postcode                          suburb state  \
0       200  AUSTRALIAN NATIONAL UNIVERSITY   ACT   
1       221                          BARTON   ACT   
2       800                          DARWIN    NT   
3       801                          DARWIN    NT   
4       804                           PARAP    NT   

                            dc                                           type  \
0  AUSTRALIAN NATIONAL UNI LPO  Post Office Boxes                               
1                          NaN  LVR                                             
2       DARWIN DELIVERY CENTRE  Delivery Area                                   
3       DARWIN DELIVERY CENTRE  Post Office Boxes                               
4                        PARAP  Post Office Boxes                               

         lat         lon  
0 -35.277272  149.117136  
1 -35.201372  149.095065  
2 -12.801028  130.955789  
3 -12.801028  130.955789  
4 -12.432181  130.843310

In [9]:
#Create dataframe for only suburbs in New South Wales
nsw_df=lat_long_df[lat_long_df['state']=='NSW'].reset_index()

In [10]:
nsw_df.head()

index  postcode  suburb state              dc  \
0    145      1001  SYDNEY   NSW    EAST SUBS MC   
1    146      1002  SYDNEY   NSW    EAST SUBS MC   
2    147      1003  SYDNEY   NSW    EAST SUBS MC   
3    148      1004  SYDNEY   NSW    EAST SUBS MC   
4    149      1005  SYDNEY   NSW  GPO BOX CENTRE   

                                            type        lat         lon  
0  LVR                                           -33.794883  151.268071  
1  LVR                                           -33.794883  151.268071  
2  LVR                                           -33.794883  151.268071  
3  LVR                                           -33.794883  151.268071  
4  LVR                                           -33.794883  151.268071

In [11]:
#remove duplicate rows from the dataframe ang group to get latitude and longitude
nsw_df.drop_duplicates(subset=['suburb'],keep='first',inplace=True)
nsw_gb=nsw_df[['suburb','lat','lon']]
nsw_gb.head()

suburb        lat         lon
0              SYDNEY -33.794883  151.268071
141         HAYMARKET -29.816475  151.659454
142  AUSTRALIA SQUARE -33.891788  151.176251
149   GROSVENOR PLACE -33.741311  151.034025
154    ROYAL EXCHANGE -33.865330  151.207905

In [12]:
#drop Sydney from the dataframe
nsw_gb=nsw_gb[nsw_gb['suburb']!='SYDNEY']
nsw_gb.head()

suburb        lat         lon
141                HAYMARKET -29.816475  151.659454
142         AUSTRALIA SQUARE -33.891788  151.176251
149          GROSVENOR PLACE -33.741311  151.034025
154           ROYAL EXCHANGE -33.865330  151.207905
159  QUEEN VICTORIA BUILDING -33.871749  151.206708

In [13]:
nsw_gb.sort_values(by='suburb',inplace=True)

In [14]:
#rename columns in the dataframe
nsw_gb.rename(columns={'suburb':'Neighbourhood','lat':'Latitude','lon':'Longitude'},inplace=True)
nsw_gb.head()

Neighbourhood   Latitude   Longitude
4840        AARONS PASS -32.863277  149.803751
707          ABBOTSBURY -33.877538  150.867768
359          ABBOTSFORD -33.852469  151.129453
4431  ABERCROMBIE RIVER -33.911806  149.332781
1267           ABERDARE -32.844200  151.376514

In [15]:
#merge the two dataframes into one
nsw_gb['Neighbourhood']=nsw_gb['Neighbourhood'].apply(lambda x:x.lower().capitalize())
sy_final=sy_df.merge(nsw_gb,on='Neighbourhood')
sy_final.head()

Neighbourhood   Latitude   Longitude
0    Abbotsbury -33.877538  150.867768
1    Abbotsford -33.852469  151.129453
2         Airds -34.084468  150.829041
3    Alexandria -33.711785  151.108248
4       Allawah -33.970018  151.114517

In [16]:
sy_final.shape

(354, 3)

In [17]:
#save the DataFrame as CSV file
sy_final.to_csv("sydney.csv",index=False)

<b><h3>4. Create a map of Sydney with neighborhoods</h3></b>

In [18]:
# get the coordinates of Sydney
address='Sydney, New South Wales'
geolocator=Nominatim(user_agent="Sydney-user")
location=geolocator.geocode(address)
latitude=location.latitude
longitude=location.longitude
print('The geograpical coordinates of Sydney are:{}, {}.'.format(latitude, longitude))

The geograpical coordinates of Sydney are:-33.8548157, 151.2164539.


In [19]:
#create map of Sydney using latitude and longitude values
map_sy=folium.Map(location=[latitude, longitude], zoom_start=10)
# add markers to map
for lat,lng,neighborhood in zip(sy_final['Latitude'],sy_final['Longitude'],sy_final['Neighbourhood']):
    label='{}'.format(neighborhood)
    label=folium.Popup(label,parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_sy)  
map_sy

<b><h3>5.Use the Foursquare API to explore the neighbourhoods</h3></b>

In [20]:
CLIENT_ID = '1CBRJARNR4YSW3ZKAUHSGKHJPPAKT1ESMJ3CKKMCZ2VLZ3FC'
CLIENT_SECRET = 'HDYRKZRGVE3SWMF3EDMB5XBXJJLMKAZQB5XJZRQLTRYROEDN'
VERSION = '20180605'
print('CLIENT_ID: '+CLIENT_ID)
print('CLIENT_SECRET:'+CLIENT_SECRET)

CLIENT_ID: 1CBRJARNR4YSW3ZKAUHSGKHJPPAKT1ESMJ3CKKMCZ2VLZ3FC
CLIENT_SECRET:HDYRKZRGVE3SWMF3EDMB5XBXJJLMKAZQB5XJZRQLTRYROEDN


<b><i>Now, let's get the top 100 venues that are within a radius of 2500 meters.</i></b>

In [21]:
radius = 2500
LIMIT = 100
venues = []
for lat,long,neighborhood in zip(sy_final['Latitude'],sy_final['Longitude'],sy_final['Neighbourhood']):
    #create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [22]:
#convert the venues list into a new DataFrame
venues_df=pd.DataFrame(venues)
# define the column names
venues_df.columns = ['Neighbourhood','Latitude','Longitude','VenueName','VenueLatitude','VenueLongitude','VenueCategory']
print(venues_df.shape)
venues_df.head()

(18902, 7)


Neighbourhood   Latitude   Longitude                 VenueName  \
0    Abbotsbury -33.877538  150.867768   Calmsley Hill City Farm   
1    Abbotsbury -33.877538  150.867768     HARV.est Cafe and Bar   
2    Abbotsbury -33.877538  150.867768  Fred's One Stop Shopping   
3    Abbotsbury -33.877538  150.867768                  7-Eleven   
4    Abbotsbury -33.877538  150.867768           Anytime Fitness   

   VenueLatitude  VenueLongitude      VenueCategory  
0     -33.868848      150.858808               Farm  
1     -33.886367      150.870152               Café  
2     -33.882396      150.888814      Grocery Store  
3     -33.883210      150.865553  Convenience Store  
4     -33.887676      150.886870                Gym

**Let's check how many venues were returned for each neighorhood**

In [23]:
venues_df.groupby(["Neighbourhood"]).count()

Latitude  Longitude  VenueName  VenueLatitude  VenueLongitude  \
Neighbourhood                                                                   
Abbotsbury            31         31         31             31              31   
Abbotsford           100        100        100            100             100   
Airds                 32         32         32             32              32   
Alexandria            41         41         41             41              41   
Allawah               49         49         49             49              49   
Ambarvale             61         61         61             61              61   
Annandale            100        100        100            100             100   
Annangrove             5          5          5              5               5   
Arcadia                7          7          7              7               7   
Arncliffe            100        100        100            100             100   
Artarmon             100        100        100            100             100   
Ashbury              100        100        100            100             100   
Ashcroft              63         63         63             63              63   
Ashfield              10         10         10             10              10   
Asquith               55         55         55             55              55   
Auburn                34         34         34             34              34   
Austral                5          5          5              5               5   
Balgowlah            100        100        100            100             100   
Balmain              100        100        100            100             100   
Bangor                13         13         13             13              13   
Banksia              100        100        100            100             100   
Banksmeadow           29         29         29             29              29   
Bankstown             47         47         47             47              47   
Bayview               48         48         48             48              48   
Beaconsfield         100        100        100            100             100   
Beecroft              30         30         30             30              30   
Belfield              85         85         85             85              85   
Belmore               72         72         72             72              72   
Belrose               12         12         12             12              12   
Berala                47         47         47             47              47   
Berowra               20         20         20             20              20   
Berrilee               3          3          3              3               3   
Bexley                93         93         93             93              93   
Bidwill               36         36         36             36              36   
Birchgrove           100        100        100            100             100   
Birrong               45         45         45             45              45   
Blackett              22         22         22             22              22   
Blacktown             80         80         80             80              80   
Blairmount            28         28         28             28              28   
Blakehurst            66         66         66             66              66   
Bondi                100        100        100            100             100   
Bonnyrigg             29         29         29             29              29   
Botany                81         81         81             81              81   
Bradbury              58         58         58             58              58   
Bringelly              5          5          5              5               5   
Bronte               100        100        100            100             100   
Brooklyn              19         19         19             19              19   
Brookvale             99         99         99 

In [24]:
print('There are {} uniques categories.'.format(len(venues_df['VenueCategory'].unique())))

There are 361 uniques categories.


In [25]:
venues_df['VenueCategory'].unique()[:50]

array(['Farm', 'Café', 'Grocery Store', 'Convenience Store', 'Gym',
       'Sandwich Place', 'Supermarket', 'Athletics & Sports',
       'Other Great Outdoors', 'Park', 'Italian Restaurant', 'Buffet',
       'Fast Food Restaurant', 'Pizza Place', 'Bar', 'Shopping Mall',
       'Pharmacy', 'Department Store', 'Sports Club', 'Martial Arts Dojo',
       'Coffee Shop', 'Sushi Restaurant', 'Seafood Restaurant', 'Market',
       'Australian Restaurant', 'Thai Restaurant', 'Gym / Fitness Center',
       'Brewery', 'Trail', 'Ice Cream Shop', 'Cricket Ground', 'Bakery',
       'Korean Restaurant', 'Mediterranean Restaurant', 'Playground',
       'South Indian Restaurant', 'Souvlaki Shop', 'Lebanese Restaurant',
       'Greek Restaurant', 'Pub', 'Sports Bar', 'Japanese Restaurant',
       'Portuguese Restaurant', 'Paper / Office Supplies Store',
       'Sporting Goods Shop', 'Boat or Ferry', 'Pier', 'Deli / Bodega',
       'Kebab Restaurant', 'Art Gallery'], dtype=object)

In [26]:
#check if the results contain Shopping Mall
"Shopping Mall" in venues_df['VenueCategory'].unique()

True

### **6.Analyze each Neighbourhood**

In [28]:
#one hot encoding
sy_onehot=pd.get_dummies(venues_df[['VenueCategory']],prefix="",prefix_sep="")
#add neighborhood column back to dataframe
sy_onehot['Neighbourhoods']=sy_final['Neighbourhood'] 
#move neighborhood column to the first column
fixed_columns=[sy_onehot.columns[-1]]+list(sy_onehot.columns[:-1])
sy_onehot=sy_onehot[fixed_columns]
print(sy_onehot.shape)
sy_onehot.head()

(18902, 362)


Neighbourhoods  ATM  Accessories Store  Afghan Restaurant  Airport  \
0     Abbotsbury    0                  0                  0        0   
1     Abbotsford    0                  0                  0        0   
2          Airds    0                  0                  0        0   
3     Alexandria    0                  0                  0        0   
4        Allawah    0                  0                  0        0   

   Airport Food Court  Airport Lounge  Airport Service  American Restaurant  \
0                   0               0                0                    0   
1                   0               0                0                    0   
2                   0               0                0                    0   
3                   0               0                0                    0   
4                   0               0                0                    0   

   Antique Shop  Aquarium  Arepa Restaurant  Argentinian Restaurant  \
0             0         0                 0                       0   
1             0         0                 0                       0   
2             0         0                 0                       0   
3             0         0                 0                       0   
4             0         0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Arts & Entertainment  \
0            0           0                    0                     0   
1            0           0                    0                     0   
2            0           0                    0                     0   
3            0           0                    0                     0   
4            0           0                    0                     0   

   Asian Restaurant  Assisted Living  Athletics & Sports  \
0                 0                0                   0   
1                 0                0                   0   
2                 0                0                   0   
3                 0                0                   0   
4                 0                0                   0   

   Australian Restaurant  Austrian Restaurant  Auto Garage  Auto Workshop  \
0                      0                    0            0              0   
1                      0                    0            0              0   
2                      0                    0            0              0   
3                      0                    0            0              0   
4                      0                    0            0              0   

   Automotive Shop  BBQ Joint  Baby Store  Badminton Court  Bakery  Bar  \
0                0          0           0                0       0    0   
1                0          0           0                0       0    0   
2                0          0           0                0       0    0   
3                0          0           0                0       0    0   
4                0          0           0                0       0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Basketball Stadium  \
0               0                 0                 0                   0   
1               0                 0                 0                   0   
2               0                 0                 0                   0   
3               0                 0                 0                   0   
4               0                 0                 0                   0   

   Bay  Beach  Beach Bar  Bed & Breakfast  Beer Bar  Beer Garden  \
0    0      0          0                0         0            0   
1    0      0          0                0         0            0   
2    0      0          0                0         0            0   
3    0      0          0                0         0            0   
4    0      0          0                0         0            0   

   Big Box Store  Bike Trail  Bistro  Board Shop  Boat or Ferry  Bookstore  \
0  

In [29]:
sy_grouped=sy_onehot.groupby(["Neighbourhoods"]).mean().reset_index()
sy_grouped

Neighbourhoods  ATM  Accessories Store  Afghan Restaurant  Airport  \
0        Abbotsbury    0                  0                  0        0   
1        Abbotsford    0                  0                  0        0   
2             Airds    0                  0                  0        0   
3        Alexandria    0                  0                  0        0   
4           Allawah    0                  0                  0        0   
5         Ambarvale    0                  0                  0        0   
6         Annandale    0                  0                  0        0   
7        Annangrove    0                  0                  0        0   
8           Arcadia    0                  0                  0        0   
9         Arncliffe    0                  0                  0        0   
10         Artarmon    0                  0                  0        0   
11          Ashbury    0                  0                  0        0   
12         Ashcroft    0                  0                  0        0   
13         Ashfield    0                  0                  0        0   
14          Asquith    0                  0                  0        0   
15           Auburn    0                  0                  0        0   
16          Austral    0                  0                  0        0   
17        Balgowlah    0                  0                  0        0   
18          Balmain    0                  0                  0        0   
19           Bangor    0                  0                  0        0   
20          Banksia    0                  0                  0        0   
21      Banksmeadow    0                  0                  0        0   
22        Bankstown    0                  0                  0        0   
23          Bayview    0                  0                  0        0   
24     Beaconsfield    0                  0                  0        0   
25         Beecroft    0                  0                  0        0   
26         Belfield    0                  0                  0        0   
27          Belmore    0                  0                  0        0   
28          Belrose    0                  0                  0        0   
29           Berala    0                  0                  0        0   
30          Berowra    0                  0                  0        0   
31         Berrilee    0                  0                  0        0   
32           Bexley    0                  0                  0        0   
33          Bidwill    0                  0                  0        0   
34       Birchgrove    0                  0                  0        0   
35          Birrong    0                  0                  0        0   
36         Blackett    0                  0                  0        0   
37        Blacktown    0                  0                  0        0   
38       Blairmount    0                  0                  0        0   
39       Blakehurst    0                  0                  0        0   
40            Bondi    0                  0                  0        0   
41        Bonnyrigg    0                  0                  0        0   
42           Botany    0                  0                  0        0   
43         Bradbury    0                  0                  0        0   
44        Bringelly    0                  0                  0        0   
45           Bronte    0                  0                  0        0   
46         Brooklyn    0                  0                  0        0   
47        Brookvale    0                  0                  0        0   
48         Bundeena    0                  0                  0        0   
49        Burraneer    0                  0                  0        0   
50          Burwood    0                  0                  0        0   
51            Busby    0                  0                  0        0   
52         Cabarita    0      

In [30]:
len(sy_grouped[sy_grouped["Shopping Mall"]>0])

11

**Create a new DataFrame for Shopping Mall data only**

In [31]:
sy_mall=sy_grouped[["Neighbourhoods","Shopping Mall"]]

In [32]:
sy_mall.head()

Neighbourhoods  Shopping Mall
0     Abbotsbury              0
1     Abbotsford              0
2          Airds              0
3     Alexandria              0
4        Allawah              0

### **7.Cluster Neighbourhoods**

*Run k-means to cluster the neighborhoods in Sydney into 2 clusters*

In [34]:
#set number of clusters
kclusters=2
sy_clustering=sy_mall.drop(["Neighbourhoods"], 1)
#run k-means clustering
kmeans=KMeans(n_clusters=kclusters,random_state=0).fit(sy_clustering)
#check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 0, 0, 0, 0, 0, 0, 0, 0, 0], dtype=int32)

In [35]:
#create a new dataframe that includes the cluster 
sy_merged=sy_mall.copy()
#add clustering labels
sy_merged["Cluster Labels"]=kmeans.labels_

In [36]:
sy_merged.rename(columns={"Neighbourhoods": "Neighbourhood"}, inplace=True)
sy_merged.head()

Neighbourhood  Shopping Mall  Cluster Labels
0    Abbotsbury              0               0
1    Abbotsford              0               0
2         Airds              0               0
3    Alexandria              0               0
4       Allawah              0               0

In [37]:
#merge to add latitude/longitude for each neighborhood
sy_merged=sy_merged.join(sy_final.set_index("Neighbourhood"),on="Neighbourhood")
sy_merged.head()

Neighbourhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0    Abbotsbury              0               0 -33.877538  150.867768
1    Abbotsford              0               0 -33.852469  151.129453
2         Airds              0               0 -34.084468  150.829041
3    Alexandria              0               0 -33.711785  151.108248
4       Allawah              0               0 -33.970018  151.114517

In [38]:
#sort the results by Cluster Labels
print(sy_merged.shape)
sy_merged.sort_values(["Cluster Labels"],inplace=True)
sy_merged

(354, 5)


Neighbourhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0        Abbotsbury              0               0 -33.877538  150.867768
237       Newington              0               0 -33.839276  151.054828
236          Nelson              0               0 -36.675498  149.971179
235          Narwee              0               0 -33.948609  151.069628
234      Narraweena              0               0 -33.749912  151.274687
233       Narrabeen              0               0 -33.723127  151.287366
232       Naremburn              0               0 -33.817299  151.201160
231        Mulgrave              0               0 -33.626053  150.829912
230          Mulgoa              0               0 -33.838167  150.683371
229          Mosman              0               0 -33.829077  151.244090
228        Mortlake              0               0 -33.843435  151.106980
227        Mortdale              0               0 -33.972239  151.075391
226       Moorebank              0               0 -33.954639  150.922360
225        Monterey              0               0 -33.973068  151.150983
224         Miranda              0               0 -34.035878  151.107201
223           Minto              0               0 -34.032022  150.848208
222     Minchinbury              0               0 -33.781673  150.813667
221        Milperra              0               0 -33.932221  151.000183
238         Newport              0               0 -33.659896  151.309312
239         Newtown              0               0 -33.896449  151.180013
240     Normanhurst              0               0 -33.720999  151.097331
241     Northbridge              0               0 -33.815028  151.222266
259        Plumpton              0               0 -33.751432  150.841204
258       Petersham              0               0 -33.896242  151.154136
257       Penshurst              0               0 -33.963346  151.086744
256         Penrith              0               0 -33.744073  150.696020
255        Pemulwuy              0               0 -33.821944  150.923752
254       Peakhurst              0               0 -33.959715  151.062187
253      Parramatta              0               0 -33.886166  151.139472
252         Parklea              0               0 -33.728123  150.923807
220      Merrylands              0               0 -33.836381  150.989219
251         Panania              0               0 -33.956130  150.998047
249         Padstow              0               0 -33.953915  151.038163
248      Paddington              0               0 -33.885032  151.226475
247          Oatley              0               0 -33.981428  151.082765
246        Oatlands              0               0 -33.796298  151.026314
245        Oakville              0               0 -33.622562  150.862154
244        Oakhurst              0               0 -33.744048  150.834819
243       Northwood              0               0 -33.829732  151.177751
242       Northmead              0               0 -33.783849  150.994336
250        Pagewood              0               0 -33.940108  151.228411
219           Menai              0               0 -34.012564  151.014645
218      Meadowbank              0               0 -33.815912  151.090715
217      Matraville              0               0 -33.957549  151.230846
194         Leumeah              0               0 -34.052285  150.833396
193      Leppington              0               0 -33.964333  150.817270
192          Leonay              0               0 -33.759156  150.652318
191      Leichhardt              0               0 -33.883793  151.157057
190    Laughtondale              0               0 -33.410229  151.024592
188       Lansdowne              0               0 -33.893687  150.971005
187         Lakemba              0               0 -33.920457  151.075921
186        Kyeemagh              0               0 -33.951452  151.159943
195        Lewisham              0               0 -33.894902  151.144413
185       

**Visualize the resulting clusters**

In [39]:
# create map
map_sy_clusters = folium.Map(location=[latitude,longitude],zoom_start=10)
#set color scheme for the clusters
x=np.arange(kclusters)
ys=[i+x+(i*x)**2 for i in range(kclusters)]
colors_array=cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow=[colors.rgb2hex(i) for i in colors_array]
# add markers to the map
markers_colors = []
for lat,lon,poi,cluster in zip(sy_merged['Latitude'],sy_merged['Longitude'],sy_merged['Neighbourhood'],sy_merged['Cluster Labels']):
    label=folium.Popup(str(poi)+' - Cluster '+str(cluster),parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_sy_clusters)      
map_sy_clusters

### **8.Examine Clusters**

*Cluster 0*

In [40]:
sy_merged.loc[sy_merged['Cluster Labels']==0]

Neighbourhood  Shopping Mall  Cluster Labels   Latitude   Longitude
0        Abbotsbury              0               0 -33.877538  150.867768
237       Newington              0               0 -33.839276  151.054828
236          Nelson              0               0 -36.675498  149.971179
235          Narwee              0               0 -33.948609  151.069628
234      Narraweena              0               0 -33.749912  151.274687
233       Narrabeen              0               0 -33.723127  151.287366
232       Naremburn              0               0 -33.817299  151.201160
231        Mulgrave              0               0 -33.626053  150.829912
230          Mulgoa              0               0 -33.838167  150.683371
229          Mosman              0               0 -33.829077  151.244090
228        Mortlake              0               0 -33.843435  151.106980
227        Mortdale              0               0 -33.972239  151.075391
226       Moorebank              0               0 -33.954639  150.922360
225        Monterey              0               0 -33.973068  151.150983
224         Miranda              0               0 -34.035878  151.107201
223           Minto              0               0 -34.032022  150.848208
222     Minchinbury              0               0 -33.781673  150.813667
221        Milperra              0               0 -33.932221  151.000183
238         Newport              0               0 -33.659896  151.309312
239         Newtown              0               0 -33.896449  151.180013
240     Normanhurst              0               0 -33.720999  151.097331
241     Northbridge              0               0 -33.815028  151.222266
259        Plumpton              0               0 -33.751432  150.841204
258       Petersham              0               0 -33.896242  151.154136
257       Penshurst              0               0 -33.963346  151.086744
256         Penrith              0               0 -33.744073  150.696020
255        Pemulwuy              0               0 -33.821944  150.923752
254       Peakhurst              0               0 -33.959715  151.062187
253      Parramatta              0               0 -33.886166  151.139472
252         Parklea              0               0 -33.728123  150.923807
220      Merrylands              0               0 -33.836381  150.989219
251         Panania              0               0 -33.956130  150.998047
249         Padstow              0               0 -33.953915  151.038163
248      Paddington              0               0 -33.885032  151.226475
247          Oatley              0               0 -33.981428  151.082765
246        Oatlands              0               0 -33.796298  151.026314
245        Oakville              0               0 -33.622562  150.862154
244        Oakhurst              0               0 -33.744048  150.834819
243       Northwood              0               0 -33.829732  151.177751
242       Northmead              0               0 -33.783849  150.994336
250        Pagewood              0               0 -33.940108  151.228411
219           Menai              0               0 -34.012564  151.014645
218      Meadowbank              0               0 -33.815912  151.090715
217      Matraville              0               0 -33.957549  151.230846
194         Leumeah              0               0 -34.052285  150.833396
193      Leppington              0               0 -33.964333  150.817270
192          Leonay              0               0 -33.759156  150.652318
191      Leichhardt              0               0 -33.883793  151.157057
190    Laughtondale              0               0 -33.410229  151.024592
188       Lansdowne              0               0 -33.893687  150.971005
187         Lakemba              0               0 -33.920457  151.075921
186        Kyeemagh              0               0 -33.951452  151.159943
195        Lewisham              0               0 -33.894902  151.144413
185       

*Cluster 1*

In [41]:
sy_merged.loc[sy_merged['Cluster Labels']==1]

Neighbourhood  Shopping Mall  Cluster Labels   Latitude   Longitude
27        Belmore              1               1 -33.916035  151.087500
155     Hillsdale              1               1 -33.952685  151.231341
288          Ruse              1               1 -34.069283  150.844069
312       Tregear              1               1 -33.751082  150.795678
311    Toongabbie              1               1 -33.788942  150.950644
268          Raby              1               1 -34.021071  150.811347
297        Sefton              1               1 -33.885501  151.011469
107        Dundas              1               1 -33.799405  151.044189
147         Gymea              1               1 -34.033142  151.085421
189      Lansvale              1               1 -33.897330  150.952786
25       Beecroft              1               1 -33.749498  151.064533

**Observations:**<br>
The shopping malls are all concentrated in the cluster 1. On the other hand, cluster 0 has no shopping mall in the neighbourhoods. This presents a great opportunity and high potential areas to open new shopping malls as there is no competition from existing malls. Therefore, this project recommends property developers to capitalize on these findings to open new shopping malls in neighbourhoods in cluster 0 with no competition. From these clusters we can see that even though the shopping malls are all concentrated in cluster 1 the total number of them in the cluster still provides an opportunity for opening malls. Also, we see more areas in the neighbourhood of Sydney lack shopping malls as cluster 0 has more neighbourhoods which provides a great scope for the property developers.